In [1]:
import os
if "/content" in os.getcwd():
  !rm -rf WHere_codes/
  !git clone https://github.com/keenranger/WHere_codes
  os.chdir("/content/WHere_codes")
  !pip install -r requirements.txt
from PDR.modules.DataLoader import *
from PDR.modules.Walker import *

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from tqdm import tqdm
import plotly.graph_objects as go

In [2]:
file_name = "200716_mag04"
pvloader = DataLoader("data/200716_mag04.csv", file_name)
pvloader.loader()
sensor_df = pvloader.sensor_df[["time", "accx", "accy", "accz", "gyrox", "gyroy",
                                "gyroz", "magx", "magy", "magz","rot0", "rot1", "rot2", "rot3", "game0", "game1", "game2", "game3"]]
sensor_df.head()

Data parsing... 
Data parsing done!


time      accx      accy       accz     gyrox     gyroy     gyroz  \
0  1594888355829 -0.406997  0.572190   9.966633 -0.018634 -0.079040 -0.117901   
1  1594888355849 -0.478820  0.828358   9.600336 -0.064449  0.007092 -0.036656   
2  1594888355869 -0.320809  0.873846   9.590760 -0.157911 -0.006958  0.009159   
3  1594888355889 -0.253774  0.892999   9.923539 -0.153024 -0.149900  0.001829   
4  1594888355909 -0.064641  0.926516  10.119855 -0.131644 -0.142570 -0.018330   

        magx       magy       magz      rot0      rot1      rot2      rot3  \
0  15.881161 -32.182580 -34.877472 -0.007628  0.038883  0.972310  0.230310   
1  16.204853 -32.459908 -35.958650 -0.007032  0.038408  0.972080  0.231378   
2  13.898495 -31.022110 -34.860382 -0.007465  0.037738  0.972067  0.231528   
3  15.298519 -32.600037 -36.592026 -0.007484  0.036504  0.972108  0.231553   
4  15.422764 -30.439964 -34.507103 -0.006111  0.035129  0.972101  0.231836   

      game0     game1     game2     game3  
0  0.014036  0.036643  0.709383  0.703730  
1  0.014018  0.036443  0.708992  0.704134  
2  0.013074  0.035921  0.708765  0.704408  
3  0.012665  0.034627  0.708875  0.704370  
4  0.013265  0.032710  0.708899  0.704426

In [3]:
walker = Walker()
for row in tqdm(sensor_df.itertuples(), total=len(sensor_df)):
    walker.step(row[0], row[1], row[2:5], row[5:8], row[8:11], row[11:15], row[15:19])


100%|██████████| 10342/10342 [00:41<00:00, 246.76it/s]


In [4]:

displacement_df = pdr_to_displacement(walker.pdr_df)
position_df = displacement_df.cumsum()
walker.pdr_df

idx  length      body       nav       rot      game    fusion
0       76.0    0.65  2.581241  2.581241  2.581241  2.581241  2.581241
1      107.0    0.65  2.520956  2.520956  2.520956  2.520956  2.520956
2      132.0    0.65  2.505455  2.505455  2.505455  2.505455  2.505455
3      156.0    0.65  2.545452  2.545452  2.545452  2.545452  2.545452
4      174.0    0.65  2.592778  2.592778  2.592778  2.592778  2.592778
..       ...     ...       ...       ...       ...       ...       ...
402  10196.0    0.65  7.364860  0.999723  1.004784  1.036919  1.033458
403  10221.0    0.65  7.552831  1.178219  1.185491  1.216514  1.213052
404  10269.0    0.65  9.036779  2.676619  2.660837  2.712105  2.708643
405  10295.0    0.65  9.132718  2.775444  2.722181  2.805620  2.802158
406  10322.0    0.65  9.197537  2.835035  2.764644  2.869126  2.865664

[407 rows x 7 columns]

In [5]:
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=position_df['rot_x'], 
    y=position_df['rot_y'],
    name="rot"))
fig.add_trace(go.Scatter(
    x=position_df['game_x'], 
    y=position_df['game_y'],
    name="game"))
fig.add_trace(go.Scatter(
    x=position_df['nav_x'], 
    y=position_df['nav_y'],
    name="nav"))

for heading, position in zip(["nav", "rot", "game"], [["nav_x","nav_y"],["rot_x","rot_y"],["game_x", "game_y"]]):    
    corner_position = position_df[position][walker.corner_df[heading]]
    fig.add_trace(go.Scatter(
    x=corner_position[position[0]], 
    y=corner_position[position[1]],
    name= heading + "corner",
    mode = 'markers')
    )
fig.update_layout(
    title="PDR",
    width = 800,
    height = 800,
    yaxis = dict(
      scaleanchor = "x",
      scaleratio = 1,
    )
)
fig.show()

In [6]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=walker.headingcalc.heading_df['time'], y=np.rad2deg(walker.headingcalc.heading_df['rot']),name="rot"))
fig.add_trace(go.Scatter(x=walker.headingcalc.heading_df['time'], y=np.rad2deg(walker.headingcalc.heading_df['game']),name="game"))
fig.add_trace(go.Scatter(x=walker.headingcalc.heading_df['time'], y=np.rad2deg(walker.headingcalc.heading_df['nav']),name="nav"))
fig.update_layout(
    width = 800,
    height = 500
)
fig.show()

In [7]:
position_df[walker.corner_df["nav"]][["nav_x","nav_y"]]

nav_x      nav_y
165 -90.889974  56.593727
206 -99.148214  32.040376
363  -8.749424 -14.675796
404   2.308651   8.779460

In [8]:
fig = go.Figure()
mag_df = pvloader.sensor_df[['time','magx', 'magy', 'magz']]
mag_norm = np.sqrt(mag_df['magx']**2 + mag_df['magy']**2 + mag_df['magz']**2)
fig.add_trace(go.Scatter(x=mag_df['time'], y=mag_df['magx'], name="magx"))
fig.add_trace(go.Scatter(x=mag_df['time'], y=mag_df['magy'], name="magy"))
fig.add_trace(go.Scatter(x=mag_df['time'], y=mag_df['magz'], name="magz"))
fig.add_trace(go.Scatter(x=mag_df['time'], y=mag_norm, name="mag norm"))
fig.update_layout(
    width = 800,
    height = 500
)
fig.show()

In [9]:
fig = go.Figure()
rot_mag_df = walker.mag_df
mag_norm = np.sqrt(rot_mag_df['rmagx']**2 + rot_mag_df['rmagy']**2 + rot_mag_df['rmagz']**2)
fig.add_trace(go.Scatter(x=rot_mag_df['time'], y=rot_mag_df['rmagx'], name="rmagx"))
fig.add_trace(go.Scatter(x=rot_mag_df['time'], y=rot_mag_df['rmagy'], name="rmagy"))
fig.add_trace(go.Scatter(x=rot_mag_df['time'], y=rot_mag_df['rmagz'], name="rmagz"))
fig.add_trace(go.Scatter(x=rot_mag_df['time'], y=mag_norm, name="rmag norm"))
fig.update_layout(
    width = 800,
    height = 500
)
fig.show()